### Analysis of Meridian Results


In [60]:
dr_total = df_post[df_post['channel'] == 'All Channels']

In [1]:
import sys, os
IN_COLAB = ('google.colab' in sys.modules) or ('COLAB_RELEASE_TAG' in os.environ)

In [2]:
# Install meridian: from PyPI @ latest release (robust in Colab and local Jupyter)
import sys, subprocess
pkg = "google-meridian[colab,and-cuda]" if IN_COLAB else "google-meridian"
print(f"Installing: {pkg}")
try:
    subprocess.check_call([sys.executable, "-m", "pip", "install", "--upgrade", pkg])
except Exception as e:
    print(f"pip install failed for {pkg}: {e}")

Installing: google-meridian


In [3]:
import arviz as az
import IPython
from meridian import constants
from meridian.analysis import analyzer
from meridian.analysis import formatter
from meridian.analysis import optimizer
from meridian.analysis import summarizer
from meridian.analysis import visualizer
from meridian.data import data_frame_input_data_builder as data_builder
from meridian.data import test_utils
from meridian.model import model
from meridian.model import prior_distribution
from meridian.model import spec
import numpy as np
import pandas as pd
# check if GPU is available
from psutil import virtual_memory
import tensorflow as tf
import tensorflow_probability as tfp

if IN_COLAB:
    from google.colab import drive


ram_gb = virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM\n'.format(ram_gb))
print(
    'Num GPUs Available: ',
    len(tf.config.experimental.list_physical_devices('GPU')),
)
print(
    'Num CPUs Available: ',
    len(tf.config.experimental.list_physical_devices('CPU')),
)





Your runtime has 16.9 gigabytes of available RAM

Num GPUs Available:  0
Num CPUs Available:  1


In [6]:
## load from local
file_path = "Results\\saved_mmm_additive.pkl"
mmm_add = model.load_mmm(file_path)

In [13]:
mmm_summarizer_add = summarizer.Summarizer(mmm_add)
analyzer_add = analyzer.Analyzer(mmm_add)
mediaEffects_add = visualizer.MediaEffects(mmm_add)
model_diagnostics_add = visualizer.ModelDiagnostics(mmm_add)
model_fit_add = visualizer.ModelFit(mmm_add)
media_summary_add = visualizer.MediaSummary(mmm_add)


c:\Users\User\repos\MMM\.venv\Lib\site-packages\meridian\analysis\analyzer.py:590: UserWarning: The `aggregate_geos` argument is ignored in the national model. It will be reset to `True`.
  warnings.warn(


In [14]:

model_diagnostics_add.plot_prior_and_posterior_distribution()

alt.FacetChart(...)

In [15]:
model_fit_add.plot_model_fit(
                         include_baseline=False,
                         include_ci=False)

alt.Chart(...)

In [23]:
df_media_results = media_summary_add.summary_table()


c:\Users\User\repos\MMM\.venv\Lib\site-packages\meridian\analysis\visualizer.py:1629: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  .aggregate(lambda g: f'{g[0]} ({g[1]}, {g[2]})')


In [17]:
model_diagnostics_add.predictive_accuracy_table()

c:\Users\User\repos\MMM\.venv\Lib\site-packages\meridian\analysis\analyzer.py:590: UserWarning: The `aggregate_geos` argument is ignored in the national model. It will be reset to `True`.
  warnings.warn(


metric geo_granularity     value
0  R_Squared        national  0.924517
1       MAPE        national  0.038723
2      wMAPE        national  0.037629

In [31]:
base_dir = 'Results'
df_rois = pd.read_csv(os.path.join(base_dir, 'rois_add.csv'))
df_decomp_vol = pd.read_csv(os.path.join(base_dir, 'decomp_add.csv'))
df_var_spec = pd.read_csv(os.path.join(base_dir, 'var_spec_add.csv'))

df_rois = df_rois.rename(columns={'variable': 'channel'})

# print('df_rois:', df_rois.shape)
# print('df_decomp_vol:', df_decomp_vol.shape)
# print('df_var_spec:', df_var_spec.shape)
# display(df_rois.head())
# display(df_decomp_vol.head())
# display(df_var_spec.head())

In [45]:
df_media_results

channel distribution impressions % impressions        spend  \
0          m_wow_tv        prior   2,699,491         15.5%   $2,699,491   
1          m_wow_tv    posterior   2,699,491         15.5%   $2,699,491   
2         m_wow_olv        prior     947,317          5.4%     $947,317   
3         m_wow_olv    posterior     947,317          5.4%     $947,317   
4      m_wow_social        prior     121,919          0.7%     $121,919   
5      m_wow_social    posterior     121,919          0.7%     $121,919   
6       m_amaze_tot        prior   7,929,905         45.6%   $7,929,905   
7       m_amaze_tot    posterior   7,929,905         45.6%   $7,929,905   
8        m_celeb_tv        prior   2,828,021         16.2%   $2,828,021   
9        m_celeb_tv    posterior   2,828,021         16.2%   $2,828,021   
10  m_celeb_outdoor        prior   1,290,619          7.4%   $1,290,619   
11  m_celeb_outdoor    posterior   1,290,619          7.4%   $1,290,619   
12  m_celeb_display        prior   1,586,718          9.1%   $1,586,718   
13  m_celeb_display    posterior   1,586,718          9.1%   $1,586,718   
14     All Channels        prior  17,403,992        100.0%  $17,403,992   
15     All Channels    posterior  17,403,992        100.0%  $17,403,992   

   % spend     cpm                     incremental outcome     % contribution  \
0    15.5%  $1,000      $4,955,573 ($814,054, $14,275,541)  0.3% (0.0%, 0.8%)   
1    15.5%  $1,000    $5,605,827 ($1,571,477, $10,371,307)  0.3% (0.1%, 0.6%)   
2     5.4%  $1,000       $1,623,880 ($274,969, $4,310,228)  0.1% (0.0%, 0.3%)   
3     5.4%  $1,000       $2,300,364 ($315,984, $6,761,048)  0.1% (0.0%, 0.4%)   
4     0.7%  $1,000            $218,272 ($31,014, $636,641)  0.0% (0.0%, 0.0%)   
5     0.7%  $1,000            $220,818 ($32,899, $647,756)  0.0% (0.0%, 0.0%)   
6    45.6%  $1,000   $14,767,082 ($1,934,515, $47,164,712)  0.9% (0.1%, 2.8%)   
7    45.6%  $1,000  $26,175,182 ($19,939,070, $32,522,926)  1.6% (1.2%, 2.0%)   
8    16.2%  $1,000      $5,280,340 ($803,332, $15,800,221)  0.3% (0.0%, 0.9%)   
9    16.2%  $1,000   $11,978,659 ($4,107,308, $21,678,384)  0.7% (0.3%, 1.3%)   
10    7.4%  $1,000       $2,355,901 ($385,829, $7,375,427)  0.1% (0.0%, 0.4%)   
11    7.4%  $1,000       $1,655,036 ($346,023, $3,923,506)  0.1% (0.0%, 0.2%)   
12    9.1%  $1,000       $2,640,401 ($459,897, $7,106,600)  0.2% (0.0%, 0.4%)   
13    9.1%  $1,000       $1,842,134 ($368,974, $4,679,372)  0.1% (0.0%, 0.3%)   
14  100.0%  $1,000  $31,841,438 ($13,173,873, $65,999,700)  1.9% (0.8%, 3.9%)   
15  100.0%  $1,000  $49,777,984 ($35,540,496, $65,934,480)  3.1% (2.2%, 4.1%)   

               roi      effectiveness            mroi           cpik  
0   1.8 (0.3, 5.3)  1.84 (0.30, 5.29)  1.0 (0.1, 2.9)   $7 ($2, $30)  
1   2.1 (0.6, 3.8)  2.08 (0.58, 3.84)  1.2 (0.3, 2.5)   $5 ($2, $16)  
2   1.7 (0.3, 4.5)  1.71 (0.29, 4.55)  0.8 (0.1, 2.1)   $7 ($2, $31)  
3   2.4 (0.3, 7.1)  2.43 (0.33, 7.14)  1.0 (0.1, 3.1)   $5 ($1, $27)  
4   1.8 (0.3, 5.2)  1.79 (0.25, 5.22)  0.5 (0.1, 1.6)   $7 ($2, $36)  
5   1.8 (0.3, 5.3)  1.81 (0.27, 5.31)  0.5 (0.1, 1.5)   $7 ($2, $33)  
6   1.9 (0.2, 5.9)  1.86 (0.24, 5.95)  0.9 (0.1, 3.0)   $8 ($2, $40)  
7   3.3 (2.5, 4.1)  3.30 (2.51, 4.10)  1.9 (1.2, 2.6)    $3 ($2, $4)  
8   1.9 (0.3, 5.6)  1.87 (0.28, 5.59)  0.9 (0.1, 2.5)   $8 ($2, $34)  
9   4.2 (1.5, 7.7)  4.24 (1.45, 7.67)  2.4 (0.6, 4.7)    $2 ($1, $7)  
10  1.8 (0.3, 5.7)  1.83 (0.30, 5.71)  0.8 (0.1, 2.5)   $8 ($2, $32)  
11  1.3 (0.3, 3.0)  1.28 (0.27, 3.04)  0.6 (0.1, 1.4)   $9 ($3, $36)  
12  1.7 (0.3, 4.5)  1.66 (0.29, 4.48)  0.8 (0.1, 2.2)   $9 ($2, $34)  
13  1.2 (0.2, 2.9)  1.16 (0.23, 2.95)  0.5 (0.1, 1.5)  $11 ($3, $42)  
14  1.8 (0.8, 3.8)     nan (nan, nan)  nan (nan, nan)   $6 ($3, $13)  
15  2.9 (2.0, 3.8)     nan (nan, nan)  nan (nan, nan)    $3 ($3, $5)

In [52]:
posterior_mask = df_media_results['distribution'].str.lower().str.contains('posterior')
df_post = df_media_results[posterior_mask].copy()
df_post = df_post[['channel','spend','incremental outcome','roi']]


In [53]:
# Clean 'incremental outcome' and 'roi' columns: extract value before bracket, remove $/commas, convert to number
import re

def clean_value(val):
    if pd.isnull(val):
        return None
    # Take value before first bracket
    s = str(val).split('(')[0].strip()
    # Remove $ and commas
    s = re.sub(r'[$,]', '', s)
    try:
        return float(s)
    except Exception:
        return None

cols_to_clean = ['incremental outcome', 'roi']
if all(col in df_post.columns for col in cols_to_clean):
    df_post_clean = df_post.copy()
    for col in cols_to_clean:
        df_post_clean[col] = df_post_clean[col].apply(clean_value)
    display(df_post_clean[['channel', 'spend', 'incremental outcome', 'roi']])
else:
    print("Some required columns missing in df_post. Available columns:", df_post.columns.tolist())

channel        spend  incremental outcome  roi
1          m_wow_tv   $2,699,491            5605827.0  2.1
3         m_wow_olv     $947,317            2300364.0  2.4
5      m_wow_social     $121,919             220818.0  1.8
7       m_amaze_tot   $7,929,905           26175182.0  3.3
9        m_celeb_tv   $2,828,021           11978659.0  4.2
11  m_celeb_outdoor   $1,290,619            1655036.0  1.3
13  m_celeb_display   $1,586,718            1842134.0  1.2
15     All Channels  $17,403,992           49777984.0  2.9

In [64]:
df_post = df_post_clean.rename(columns={'spend': 'spend (mer)','incremental outcome':'value (mer)', 'roi':'roi (mer)'})
# df_post[df_post['channel'] == 'All Channels'].loc['channel']="Total"
idx = df_post.index[df_post['channel'] == 'All Channels']
df_post.loc[idx, 'channel'] = 'Total'


In [75]:
merged = df_rois.merge(df_post, on='channel', how='left', suffixes=('', '_rois'))
display(merged)


channel       value   spend_sum   roi  roi (est)  \
0         m_wow_tv   8,153,785   2,699,491  3.02       3.88   
1        m_wow_olv   2,121,312     947,317  2.24       4.14   
2     m_wow_social     213,268     121,919  1.75     -12.65   
3      m_amaze_tot  25,532,763   7,929,905  3.22       3.24   
4       m_celeb_tv   9,193,975   2,828,021  3.25       3.45   
5  m_celeb_outdoor   4,194,756   1,290,619  3.25       0.56   
6  m_celeb_display   2,606,237   1,586,718  1.64       5.98   
7            Total  52,016,095  17,403,991  2.99       3.36   

  % change (est/actual)  spend (mer)  value (mer)  roi (mer)  
0                28.48%          NaN    5605827.0        2.1  
1                84.82%          NaN    2300364.0        2.4  
2              -822.86%          NaN     220818.0        1.8  
3                 0.62%          NaN   26175182.0        3.3  
4                 6.15%          NaN   11978659.0        4.2  
5               -82.77%          NaN    1655036.0        1.3  
6               264.63%          NaN    1842134.0        1.2  
7                12.37%          NaN   49777984.0        2.9

In [74]:
# Format value (mer) and roi (mer) as numbers and create percent change columns
for col in ['value (mer)', 'roi (mer)', 'spend (mer)', 'spend_sum', 'value', 'roi']:
    if col in merged.columns:
        merged[col] = pd.to_numeric(merged[col], errors='coerce')

# # Percent change calculations
# merged['%_change_spend'] = 100 * (merged['spend (mer)'] - merged['spend_sum']) / merged['spend_sum']
# merged['%_change_value'] = 100 * (merged['value (mer)'] - merged['value']) / merged['value']
# merged['%_change_roi'] = 100 * (merged['roi (mer)'] - merged['roi']) / merged['roi']

# # Optional: format as string with 2 decimals
# merged['value (mer)'] = merged['value (mer)'].map('{:,.2f}'.format)
# merged['roi (mer)'] = merged['roi (mer)'].map('{:,.2f}'.format)
# merged['%_change_spend'] = merged['%_change_spend'].map('{:+.1f}%'.format)
# merged['%_change_value'] = merged['%_change_value'].map('{:+.1f}%'.format)
# merged['%_change_roi'] = merged['%_change_roi'].map('{:+.1f}%'.format)

display(merged)

channel  value  spend_sum   roi  roi (est) % change (est/actual)  \
0         m_wow_tv    NaN        NaN  3.02       3.88                28.48%   
1        m_wow_olv    NaN        NaN  2.24       4.14                84.82%   
2     m_wow_social    NaN        NaN  1.75     -12.65              -822.86%   
3      m_amaze_tot    NaN        NaN  3.22       3.24                 0.62%   
4       m_celeb_tv    NaN        NaN  3.25       3.45                 6.15%   
5  m_celeb_outdoor    NaN        NaN  3.25       0.56               -82.77%   
6  m_celeb_display    NaN        NaN  1.64       5.98               264.63%   
7            Total    NaN        NaN  2.99       3.36                12.37%   

   spend (mer)  value (mer)  roi (mer)  
0          NaN    5605827.0        2.1  
1          NaN    2300364.0        2.4  
2          NaN     220818.0        1.8  
3          NaN   26175182.0        3.3  
4          NaN   11978659.0        4.2  
5          NaN    1655036.0        1.3  
6          NaN    1842134.0        1.2  
7          NaN   49777984.0        2.9

In [ ]:
# Define a reusable function to clean and convert numeric-like columns in any DataFrame
import re
import numpy as np
import pandas as pd


def clean_numeric_dataframe(df: pd.DataFrame,
                            exclude=None,
                            in_place: bool = True) -> pd.DataFrame:
    """
    Clean and convert numeric-like columns in a DataFrame.

    - Strips currency symbols ($, €, £), commas, percent signs, spaces
    - Removes trailing credible interval text: e.g., "123.4 (1.1, 2.2)"
    - Handles accounting negatives like "(1,234.56)"
    - Normalizes unicode minus
    - Coerces to float; non-convertible values become NaN

    Parameters
    ----------
    df : pd.DataFrame
        Input DataFrame.
    exclude : Iterable[str] | None
        Column names to skip (e.g., identifiers like 'channel'). Case-insensitive.
    in_place : bool
        If True, modify df in place and return it; otherwise operate on a copy.

    Returns
    -------
    pd.DataFrame
        DataFrame with cleaned numeric columns.
    """
    if exclude is None:
        exclude = []
    exclude_lc = {str(c).lower() for c in exclude}

    out = df if in_place else df.copy()

    def _clean_numeric_str(val):
        if pd.isna(val):
            return np.nan
        s = str(val).strip()
        if s == '' or s.lower() in {'nan', 'none', 'null', 'na'} or s in {'—', '–', '-'}:
            return np.nan
        # Accounting negatives like (1,234.56)
        is_accounting_neg = False
        if re.fullmatch(r"\(\s*[\d$€£,.%\s\-]+\s*\)", s):
            is_accounting_neg = True
            s = s[1:-1].strip()
        # Remove trailing CI text: "123.4 (1.1, 2.2)"
        if ' (' in s:
            s = s.split(' (', 1)[0].strip()
        # Normalize unicode minus
        s = s.replace('\u2212', '-')
        # Strip currency, percent, thousands separators
        s = re.sub(r'[,$€£%]', '', s)
        # Remove spaces
        s = s.replace(' ', '')
        # Keep numeric characters only
        s = re.sub(r'[^0-9eE+\-\.]', '', s)
        if s in {'', '-', '+', '.', '+.', '-.'}:
            return np.nan
        try:
            num = float(s)
            return -num if is_accounting_neg else num
        except Exception:
            return np.nan

    for c in out.columns:
        if str(c).lower() in exclude_lc:
            continue
        # Apply cleaning for object columns
        if out[c].dtype == 'object':
            out[c] = out[c].apply(_clean_numeric_str)
        # Final coercion to numeric
        out[c] = pd.to_numeric(out[c], errors='coerce')

    return out


# Example usage for this notebook: clean `merged`, excluding identifier columns
if 'merged' in globals():
    clean_numeric_dataframe(merged, exclude=['channel', 'variable'], in_place=True)
    display(merged.dtypes)
    display(merged.head(10))
else:
    print("DataFrame 'merged' not found. Run previous cells that create it and try again.")

channel                   object
value                    float64
spend_sum                float64
roi                      float64
roi (est)                float64
% change (est/actual)    float64
spend (mer)              float64
value (mer)              float64
roi (mer)                float64
dtype: object

channel       value   spend_sum   roi  roi (est)  \
0         m_wow_tv   8153785.0   2699491.0  3.02       3.88   
1        m_wow_olv   2121312.0    947317.0  2.24       4.14   
2     m_wow_social    213268.0    121919.0  1.75     -12.65   
3      m_amaze_tot  25532763.0   7929905.0  3.22       3.24   
4       m_celeb_tv   9193975.0   2828021.0  3.25       3.45   
5  m_celeb_outdoor   4194756.0   1290619.0  3.25       0.56   
6  m_celeb_display   2606237.0   1586718.0  1.64       5.98   
7            Total  52016095.0  17403991.0  2.99       3.36   

   % change (est/actual)  spend (mer)  value (mer)  roi (mer)  
0                  28.48          NaN    5605827.0        2.1  
1                  84.82          NaN    2300364.0        2.4  
2                -822.86          NaN     220818.0        1.8  
3                   0.62          NaN   26175182.0        3.3  
4                   6.15          NaN   11978659.0        4.2  
5                 -82.77          NaN    1655036.0        1.3  
6                 264.63          NaN    1842134.0        1.2  
7                  12.37          NaN   49777984.0        2.9